In [25]:
from selenium.webdriver.common.by import By
import time
from datetime import datetime,timezone
from os import name
from selenium import webdriver
from selenium.webdriver.support.wait import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import json
import requests
import mysql.connector

import sys
import os
import pandas as pd


In [26]:
def crear_driver_chrome(headless=True):
    # for windows
    if name == 'nt':
        PATH = r"chromedriver.exe"

    # for mac and linux(here, os.name is 'posix')
    else:
        PATH = r"./chromedriver"

    options = webdriver.ChromeOptions()
    if headless:
        options.add_argument('--no-sandbox')
        options.add_argument('--headless')
        options.add_argument('--disable-gpu')
        options.add_argument('--disable-dev-shm-usage')
    
    options.add_experimental_option('excludeSwitches', ['enable-logging'])

    options.add_argument('--lang=es')
    options.add_experimental_option('prefs', {'intl.accept_languages': 'es,es_ES'})
    
    driver = webdriver.Chrome(executable_path=PATH, options=options)

    driver.set_window_size(1920, 1080)
    driver.maximize_window()

    return driver

In [27]:
#Entramos en la web
driver = crear_driver_chrome(False)
driver.get("https://www.conexoo.com/")
time.sleep(3)
print('entra en web')
privacidad = driver.find_element(By.LINK_TEXT, value='Acceso Clientes')
privacidad.click()
time.sleep(1)
print('paso privacidad')
time.sleep(2)
print('entra en acceso a clientes')


time.sleep(3)

/tmp/ipykernel_38404/3057013930.py:22: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(executable_path=PATH, options=options)


entra en web
paso privacidad
entra en acceso a clientes


In [28]:
driver.find_element(By.ID, "login").send_keys('info@posicionamientowebibiza.com')
time.sleep(1.5)
driver.find_element(By.ID, 'password').send_keys('amelie1313')
time.sleep(3)



In [29]:

par = driver.current_url
rellenar_resultado_recaptcha = WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, 'g-recaptcha-response'))
)


In [30]:
clicar = driver.find_element(By.CLASS_NAME, 'g-recaptcha')
clicar.click()
time.sleep(5)

In [32]:
logear =driver.find_element(By.CLASS_NAME, 'btn-lg')
logear.click()
time.sleep(4)

In [34]:
comprar_articulos = driver.find_element(By.XPATH, '//span[normalize-space()="Comprar artículos"]')
comprar_articulos.click()
time.sleep(2)


In [35]:
tipoMedios = ['Webs y Blogs', 'Periódicos']
dataFinalArr = {}

In [36]:
#En principio no hace falta este bloque
#webs = driver.find_element(By.XPATH, '//*[@id="sidebarnav"]/li[4]/ul/li[1]/a')#//*[@id="menubar"]/div/div/div[1]/ul/li[3]
#webs.click()
#print('pulsado en el menú las webs')
#time.sleep(2)

In [37]:
for tipoMedio in tipoMedios:
    #Clics en webs y Blogs/Periodicos
    driver.execute_script("$('ul#sidebarnav a:contains(\"" + tipoMedio + "\")')[0].click();")
    time.sleep(5)
    
    #Clic en btn_view_list
    btn = driver.find_element(By.XPATH, '//*[@id="btn_view_list"]')
    btn.click()
    time.sleep(3)
    
    #Clic resetear filtros
    reset = driver.find_element(By.ID, 'btn_reset_filters')
    preloaderEstado = 'block'
    while(preloaderEstado!='none'):
        time.sleep(8)
        preloaderEstado = driver.execute_script("return $('#table_websites_processing').css('display')")
    print(time.strftime("%d/%m/%y - %H:%M:%S") + ' | Escaneando todos los medios de -> ' + tipoMedio)
    dataFinalArr[tipoMedio] =driver.execute_script("""let medios = []; 
                                                    $('#table_websites').DataTable().rows().data().each(function(medio){
                                                        medios.push(medio);
                                                        });
                                                    return medios;""")
    

03/06/23 - 14:01:59 | Escaneando todos los medios de -> Webs y Blogs
03/06/23 - 14:02:23 | Escaneando todos los medios de -> Periódicos


In [38]:
#Transformando los arrays en listas
dataFinal = []
for unDataFinal in dataFinalArr:
    dataFinal.extend(dataFinalArr[unDataFinal])

print(dataFinal)


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [39]:
for campo_array in ['categorias_agregadas', 'tematicas_no_aceptadas']:
        for idData, data in enumerate(dataFinal):
            if len(data[campo_array]) > 0:
                dataFinal[idData][campo_array + '_arr'] = []
                for categoria in data[campo_array]:
                    dataFinal[idData][campo_array + '_arr'].append(categoria['description'])
            else:
                dataFinal[idData]['categorias_agregadas_arr'] = []

In [40]:
dataFinal

[{'analytics': None,
  'art_ya_pub': True,
  'aviso_publicidad': 2,
  'bl': 180000,
  'categorias_agregadas': [{'description': 'Economía',
    'id': 15,
    'name': 'economia',
    'pivot': {'category_id': 15,
     'created_at': '2020-06-16 20:10:08',
     'updated_at': '2020-06-16 20:10:08',
     'web_id': 538}},
   {'description': 'Emprendedores y pymes',
    'id': 17,
    'name': 'emprendedoresypymes',
    'pivot': {'category_id': 17,
     'created_at': '2020-06-25 12:21:03',
     'updated_at': '2020-06-25 12:21:03',
     'web_id': 538}}],
  'cf': 43,
  'clase_web': 2,
  'clase_web_text': 'Periódico',
  'codigo_analytics': None,
  'codigo_integracion': None,
  'crank': 98,
  'created_at': '2020-06-16 20:10:08',
  'da': 0,
  'deleted_at': None,
  'descripcion': 'Soluciones para profesionales y emprendedores',
  'discard': False,
  'dr': '72.0',
  'favorite': False,
  'fecha_act_ahrefs': '2020-07-20',
  'fecha_act_majestic': '2020-09-07',
  'fecha_act_sistrix': '2022-08-06',
  'group_

In [41]:
lista = []
contador = 1
for medio in dataFinal:
    for dato in ['url_link', 'descripcion', 'idioma', 'idioma_traducido', 'pais_audiencia,da', 'cf', 'dr', 'pa', 'ur', 'tf', 'rd', 'obl', 'precio_post', 'precio_post_cliente', 'max_links_post', 'tipo_sitio', 'tipo_sitio_text', 'crank', 'keywords', 'traffic_organic', 'majestic_links', 'majestic_rd,analytics', 'art_ya_pub', 'aviso_publicidad', 'bl', 'clase_web', 'clase_web_text', 'codigo_analytics', 'codigo_integracion', 'created_at', 'deleted_at', 'discard,favorite', 'fecha_act_ahrefs', 'fecha_act_majestic', 'fecha_act_sistrix,group_check', 'home_appearance', 'image', 'newsletter_difusion', 'ps_rank', 'social_publication', 'tarjetas_rojas', 'texto_conexoo', 'updated_at', 'userId,valoraciones_count', 'visitas_dia']:
        if not dato in medio:
            medio[dato] = None
    for dato in ['categorias_agregadas_arr', 'tematicas_no_aceptadas_arr']:
        if not dato in medio:
            medio[dato] = []

    lista.append(
        (
            medio['id'], 
            medio['url'], 
            medio['url_link'], 
            medio['descripcion'], 
            medio['idioma'], 
            medio['idioma_traducido'], 
            medio['pais_audiencia'], 
            medio['da'], 
            medio['cf'], 
            medio['dr'], 
            medio['pa'], 
            medio['ur'], 
            medio['tf'], 
            medio['rd'], 
            medio['obl'], 
            float(medio['precio_post']), 
            float(medio['precio_post_cliente']), 
            medio['max_links_post'], 
            medio['tipo_sitio'], 
            medio['tipo_sitio_text'], 
            medio['crank'], 
            medio['keywords'], 
            medio['traffic_organic'], 
            medio['majestic_links'], 
            medio['majestic_rd'], 
            medio['art_ya_pub'], 
            medio['aviso_publicidad'], 
            medio['bl'], 
            medio['clase_web'], 
            medio['clase_web_text'], 
            medio['created_at'], 
            medio['discard'], 
            medio['favorite'], 
            medio['group_check'], 
            medio['home_appearance'], 
            medio['image'], 
            medio['newsletter_difusion'],  
            medio['ps_rank'], 
            medio['social_publication'], 
            medio['tarjetas_rojas'], 
            medio['texto_conexoo'], 
            medio['updated_at'], 
            medio['userId'], 
            medio['valoraciones_count'], 
            medio['visitas_dia'], 
            '-|-'.join(medio['categorias_agregadas_arr']), 
            '-|-'.join(medio['tematicas_no_aceptadas_arr'])
        )
    )
    contador += 1

In [42]:
lista

[(538,
  'https://www.larepublica.net/',
  'https://nulllreferer.com/?https://www.larepublica.net/',
  'Soluciones para profesionales y emprendedores',
  'es',
  'español (o castellano)',
  'ES',
  0,
  43,
  '72.0',
  0,
  23,
  52,
  19852,
  5411,
  510.0,
  816.0,
  4,
  1,
  'Follow/NoFollow',
  98,
  194690,
  291423,
  122979,
  2876,
  True,
  2,
  180000,
  2,
  'Periódico',
  '2020-06-16 20:10:08',
  False,
  False,
  True,
  True,
  '/images/websites/538.jpg',
  False,
  0,
  True,
  0,
  False,
  '2023-01-25 12:30:44',
  12,
  0,
  0,
  '',
  ''),
 (11258,
  'http://www.lacapital.com.ar',
  'https://nulllreferer.com/?http://www.lacapital.com.ar',
  'La Capital es un diario de la ciudad de Rosario y su región, en la República Argentina. Fue fundado el 15 de noviembre de 1867 y es el periódico más antiguo de Argentina todavía en circulación, por lo que ha ganado el título de "Decano de la Prensa Argentina"',
  'es',
  'español (o castellano)',
  'AR',
  0,
  58,
  '72.0',
  0

In [43]:
columns_name = ['id','url','url_link', 'descripcion', 'idioma','idioma_traducido', 
            'pais_audiencia','da','cf','dr','pa','ur','tf','rd','obl','precio_post', 
            'precio_post_cliente','max_links_post','tipo_sitio','tipo_sitio_text', 
            'crank','keywords','traffic_organic','majestic_links','majestic_rd', 
            'art_ya_pub','aviso_publicidad','bl','clase_web','clase_web_text', 
            'created_at','discard','favorite','group_check','home_appearance','image', 
            'newsletter_difusion','ps_rank','social_publication','tarjetas_rojas','texto_conexoo', 
            'updated_at','userId','valoraciones_count','visitas_dia','categorias_agregadas_arr','tematicas_no_aceptadas_arr'] 

df = pd.DataFrame(lista, columns=columns_name)
df

id                                            url  \
0       538                   https://www.larepublica.net/   
1     11258                    http://www.lacapital.com.ar   
2       771              https://www.marketingdirecto.com/   
3       532                      https://www.elplural.com/   
4      7646                    https://www.europapress.es/   
...     ...                                            ...   
1465   1300         https://www.territoriomag.es/internet/   
1466  11325  https://www.imagendelosvallecaucanos.com/web/   
1467     27                      https://mundocripto.news/   
1468   1293         https://www.territoriomag.es/femenino/   
1469  11247                 http://www.eltribuno.com/salta   

                                               url_link  \
0     https://nulllreferer.com/?https://www.larepubl...   
1     https://nulllreferer.com/?http://www.lacapital...   
2     https://nulllreferer.com/?https://www.marketin...   
3     https://nulllreferer.com/?https://www.elplural...   
4     https://nulllreferer.com/?https://www.europapr...   
...                                                 ...   
1465  https://nulllreferer.com/?https://www.territor...   
1466  https://nulllreferer.com/?https://www.imagende...   
1467  https://nulllreferer.com/?https://mundocripto....   
1468  https://nulllreferer.com/?https://www.territor...   
1469  https://nulllreferer.com/?http://www.eltribuno...   

                                            descripcion idioma  \
0         Soluciones para profesionales y emprendedores     es   
1     La Capital es un diario de la ciudad de Rosari...     es   
2            Noticias de marketing, publicidad y marcas     es   
3                       Periódico digital de actualidad     es   
4     Europa Press defiende la pluralidad e independ...     es   
...                                                 ...    ...   
1465  Territorio Internet es un magazine especializa...     es   
1466  Revista Imagen de los Vallecaucanos se creó en...     es   
1467  Somos un grupo de profesionales apasionados de...     es   
1468  Territorio Femenino es un magazine especializa...     es   
1469  El Tribuno es un diario argentino con sede en ...     es   

            idioma_traducido pais_audiencia   da  cf    dr  ...  ps_rank  \
0     español (o castellano)             ES  0.0  43  72.0  ...      0.0   
1     español (o castellano)             AR  0.0  58  72.0  ...      0.0   
2     español (o castellano)             ES  0.0  52  77.0  ...      0.0   
3     español (o castellano)             ES  0.0  50  72.0  ...      0.0   
4     español (o castellano)             ES  0.0  63  86.0  ...      0.0   
...                      ...            ...  ...  ..   ...  ...      ...   
1465  español (o castellano)             ES  0.0  13   0.0  ...      0.0   
1466  español (o castellano)             CO  0.0   0   0.0  ...      0.0   
1467  español (o castellano)             US  0.0  10   0.0  ...      0.0   
1468  español (o castellano)             ES  0.0  13   0.0  ...      0.0   
1469  español (o castellano)             AR  0.0   0   0.0  ...      0.0   

      social_publication  tarjetas_rojas  texto_conexoo           updated_at  \
0                   True               0          False  2023-01-25 12:30:44   
1                  False               0          False  2023-04-10 20:47:12   
2                   True               1          False  2023-01-25 14:00:26   
3                   True               0          False  2023-01-25 14:01:11   
4                   True               0          False  2023-03-29 16:32:02   
...                  ...             ...            ...                  ...   
1465                True               0          False  2022-07-28 12:32:08   
1466                True               0          False  2023-03-23 11:51:35   
1467                True               0          False  2023-01-25 14:01:12   
1468                True               0         

In [44]:
df.to_csv('conexoo.csv')


In [45]:
url_link = df['url']
url_link.to_csv('urls.csv')